In [6]:
import sqlite3

# Connect to the database
conn = sqlite3.connect('company.db')

# Create a cursor object
cursor = conn.cursor()

print("Connected to company.db")

Connected to company.db


In [7]:
# Journées
import datetime
cursor.execute("SELECT NUMERO_EMPLOYE, NOM, PRENOM, CS_PRODUCTION,CS_JOURNEE, DATE_DEBUT FROM EMPLOYE")
employees = cursor.fetchall()

cursor.execute("SELECT * FROM LOG_JOURNEE_JOUR")
LOG_JOURNEE_JOUR=cursor.fetchall()

# Find the smallest date
smallest_date = min(row[1] for row in LOG_JOURNEE_JOUR)
today = datetime.datetime.now().strftime("%Y-%m-%d")
delta = datetime.datetime.strptime(today, "%Y-%m-%d") - datetime.datetime.strptime(smallest_date, "%Y-%m-%d")
for i in range(delta.days + 1):
    date = (datetime.datetime.strptime(smallest_date, "%Y-%m-%d") + datetime.timedelta(days=i)).strftime("%Y-%m-%d")
    if datetime.datetime.strptime(date, "%Y-%m-%d").weekday() == 0:
        for employee in employees:
            NUMERO_EMPLOYE, NOM, PRENOM,CS_PRODUCTION,CS_JOURNEE, DATE_DEBUT = employee
            cursor.execute("SELECT * FROM SALAIRE_SEMAINE where DATE_LUNDI=? and NUMERO_EMPLOYE=?", (date,NUMERO_EMPLOYE))
            semaine=cursor.fetchall()
            print(semaine)
            if semaine ==[] and CS_JOURNEE is not None:
                cursor.execute(f"SELECT SALAIRE_HORAIRE FROM GRILLE_SALAIRE_HORAIRE WHERE CS_HORAIRE = {CS_JOURNEE}")
                salaire_horaire=cursor.fetchone()[0]
                liste_jours_travail=[]
                for j in range(2,8):
                    jour_semaine=(datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.timedelta(days=j)).strftime("%Y-%m-%d")
                    jour_semaine_date = datetime.datetime.strptime(jour_semaine, "%Y-%m-%d")
                    if jour_semaine_date.month == 12 and jour_semaine_date.day == 25:
                        noel=round(min(max(0, (datetime.datetime.strptime(DATE_DEBUT, "%Y-%m-%d")-datetime.datetime.strptime(jour_semaine, "%Y-%m-%d")).days /365 *salaire_horaire*48 ),salaire_horaire*48*4.5))
                    else:
                        noel=0
                    if (datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.datetime.strptime(DATE_DEBUT, "%Y-%m-%d")).days>=365 and (datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.datetime.strptime(DATE_DEBUT, "%Y-%m-%d")).days % 365 in range(0, 6):
                        anciennete=round(48*salaire_horaire)
                    else:
                        anciennete=0
                    cursor.execute("SELECT * FROM LOG_JOURNEE_JOUR where DATE=? and NUMERO_EMPLOYE=?", (jour_semaine, NUMERO_EMPLOYE))
                    jour=cursor.fetchall()
                    liste_jours_travail.insert(0, jour)
                print(liste_jours_travail)
                if liste_jours_travail!=[[], [], [], [], [], []]:
                    NB_heures=0
                    heures_sup=0
                    retard=0
                    heures_base=0
                    for k in liste_jours_travail:
                        if k!=[]:
                            heures_base=heures_base+k[0][7]
                            NB_heures=NB_heures+k[0][8]
                            heures_sup=heures_sup+k[0][9]
                            if k[0][10]==True or k[0][10]==1:
                                retard=+1
                    
                    #print(datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.timedelta(days=7),NUMERO_EMPLOYE,NB_PIECES,0,salaire_horaire*NB_PIECES,noel,anciennete,salaire_horaire*NB_PIECES+noel+anciennete)
                    cursor.execute("SELECT DATE_LUNDI,SALAIRE_SEMAINE.NUMERO_EMPLOYE from SALAIRE_SEMAINE where DATE_LUNDI=? and NUMERO_EMPLOYE=?", (datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.timedelta(days=7),NUMERO_EMPLOYE))
                    semaine_verif=cursor.fetchall()
                    if semaine_verif==[]:
                        cursor.execute("INSERT INTO SALAIRE_SEMAINE (DATE_LUNDI,NUMERO_EMPLOYE,NB_HEURES, NB_PRODUCTION,RETARD,HEURES_SUP, PIECES_SUP,SALAIRE_BASE, SALAIRE_AVANT,NOEL,ANCIENNETE,SALAIRE_APRES) VALUES (?,?,?,?,?,?,?,?,?,?,?,?)",
                                        ((datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.timedelta(days=7)),NUMERO_EMPLOYE,NB_heures,0,retard,heures_sup,0,salaire_horaire*heures_base, salaire_horaire*(NB_heures+heures_sup)-retard*5,noel,anciennete,salaire_horaire*(NB_heures+heures_sup)-retard*5+noel+anciennete))
            if semaine ==[] and CS_PRODUCTION is not None:
                cursor.execute(f"SELECT SALAIRE_PIECE,PIECE_JOUR FROM GRILLE_SALAIRE_PROD WHERE CS_PRODUCTION = {CS_PRODUCTION}")
                salaire_PROD ,PIECE_JOUR =cursor.fetchone()
                liste_jours_travail=[]
                for j in range(2,8):
                    jour_semaine=(datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.timedelta(days=j)).strftime("%Y-%m-%d")
                    jour_semaine_date = datetime.datetime.strptime(jour_semaine, "%Y-%m-%d")
                    if jour_semaine_date.month == 12 and jour_semaine_date.day == 25:
                        noel=round(min(max(0, (datetime.datetime.strptime(DATE_DEBUT, "%Y-%m-%d")-datetime.datetime.strptime(jour_semaine, "%Y-%m-%d")).days /365 *salaire_PROD*PIECE_JOUR ),salaire_PROD*PIECE_JOUR*4.5))
                    else:
                        noel=0
                    if (datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.datetime.strptime(DATE_DEBUT, "%Y-%m-%d")).days>=365 and (datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.datetime.strptime(DATE_DEBUT, "%Y-%m-%d")).days % 365 in range(0, 6):
                        anciennete=round(PIECE_JOUR*salaire_PROD)
                    else:
                        anciennete=0
                    cursor.execute("SELECT * FROM LOG_JOURNEE_PROD where DATE=? and NUMERO_EMPLOYE=?", (jour_semaine, NUMERO_EMPLOYE))
                    jour=cursor.fetchall()
                    liste_jours_travail.insert(0, jour)
                print(liste_jours_travail)
                if liste_jours_travail!=[[], [], [], [], [], []]:
                    NB_PIECES=0
                    retard=0
                    pieces_sup=0
                    pieces_base=0
                    for k in liste_jours_travail:
                        if k!=[]:
                            pieces_base=pieces_base+k[0][4]
                            NB_PIECES=NB_PIECES+k[0][5]
                            pieces_sup=pieces_sup+k[0][6]
                            if k[0][9]==True or k[0][9]==1:
                                retard=+1
                    #print(datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.timedelta(days=7),NUMERO_EMPLOYE,NB_PIECES,0,salaire_horaire*NB_PIECES,noel,anciennete,salaire_horaire*NB_PIECES+noel+anciennete)
                    cursor.execute("SELECT DATE_LUNDI,SALAIRE_SEMAINE.NUMERO_EMPLOYE from SALAIRE_SEMAINE where DATE_LUNDI=? and NUMERO_EMPLOYE=?", (datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.timedelta(days=7),NUMERO_EMPLOYE))
                    semaine_verif=cursor.fetchall()
                    if semaine_verif==[]:
                        cursor.execute("INSERT INTO SALAIRE_SEMAINE (DATE_LUNDI,NUMERO_EMPLOYE,NB_HEURES, NB_PRODUCTION,RETARD,HEURES_SUP, PIECES_SUP,SALAIRE_BASE,SALAIRE_AVANT,NOEL,ANCIENNETE,SALAIRE_APRES) VALUES (?,?,?,?,?,?,?,?,?,?,?,?)", 
                                       ((datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.timedelta(days=7)),NUMERO_EMPLOYE,0,NB_PIECES,retard,0,pieces_sup,salaire_PROD*pieces_base,salaire_PROD*(NB_PIECES+pieces_sup)-retard*5,noel,anciennete,salaire_PROD*(NB_PIECES+pieces_sup)-retard*5+noel+anciennete))

conn.commit()
conn.close()

[]
[[], [], [], [], [(1, '2020-11-13', 4, 1, '8:30', '8:00', '17:00', 9, 8.5, 0, 1), (2664, '2020-11-13', 4, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0)], [(2, '2020-11-14', 5, 1, '8:00', '8:00', '11:00', 3, 3, 0, 0), (2665, '2020-11-14', 5, 1, '8:00', '8:00', '11:00', 3, 3, 0, 0)]]
[]
[[], [], [], [], [], []]
[]
[[(319, '2020-11-09', 0, 3, 15, 15, 0, '8:00', '8:00', 0)], [(320, '2020-11-10', 1, 3, 15, 15, 0, '8:00', '8:00', 0)], [(321, '2020-11-11', 2, 3, 15, 15, 0, '8:00', '8:00', 0)], [(322, '2020-11-12', 3, 3, 15, 15, 0, '8:00', '8:00', 0)], [(323, '2020-11-13', 4, 3, 15, 15, 0, '8:00', '8:00', 0)], [(324, '2020-11-14', 5, 3, 15, 15, 0, '8:00', '8:00', 0)]]
[]
[[], [], [], [], [], []]
[]
[[], [], [], [], [], []]
[]
[[], [], [], [], [], []]
[]
[[], [], [], [], [], []]
[]
[[], [], [], [], [], []]
[]
[[(3, '2020-11-16', 0, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0), (2666, '2020-11-16', 0, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0)], [(4, '2020-11-17', 1, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0)

C:\Users\neiro\AppData\Local\Temp\ipykernel_1912\764195697.py:54: DeprecationWarning: The default datetime adapter is deprecated as of Python 3.12; see the sqlite3 documentation for suggested replacement recipes
  cursor.execute("SELECT DATE_LUNDI,SALAIRE_SEMAINE.NUMERO_EMPLOYE from SALAIRE_SEMAINE where DATE_LUNDI=? and NUMERO_EMPLOYE=?", (datetime.datetime.strptime(date, "%Y-%m-%d") - datetime.timedelta(days=7),NUMERO_EMPLOYE))
C:\Users\neiro\AppData\Local\Temp\ipykernel_1912\764195697.py:57: DeprecationWarning: The default datetime adapter is deprecated as of Python 3.12; see the sqlite3 documentation for suggested replacement recipes
  cursor.execute("INSERT INTO SALAIRE_SEMAINE (DATE_LUNDI,NUMERO_EMPLOYE,NB_HEURES, NB_PRODUCTION,RETARD,HEURES_SUP, PIECES_SUP,SALAIRE_BASE, SALAIRE_AVANT,NOEL,ANCIENNETE,SALAIRE_APRES) VALUES (?,?,?,?,?,?,?,?,?,?,?,?)",
C:\Users\neiro\AppData\Local\Temp\ipykernel_1912\764195697.py:91: DeprecationWarning: The default datetime adapter is deprecated as 

[[], [], [], [], [], []]
[]
[[], [], [], [], [], []]
[]
[[], [], [], [], [], []]
[]
[[], [], [], [], [], []]
[]
[[(81, '2021-02-15', 0, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0), (2744, '2021-02-15', 0, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0)], [(82, '2021-02-16', 1, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0), (2745, '2021-02-16', 1, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0)], [(83, '2021-02-17', 2, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0), (2746, '2021-02-17', 2, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0)], [(84, '2021-02-18', 3, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0), (2747, '2021-02-18', 3, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0)], [(85, '2021-02-19', 4, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0), (2748, '2021-02-19', 4, 1, '8:00', '8:00', '17:00', 9, 9, 0, 0)], [(86, '2021-02-20', 5, 1, '8:00', '8:00', '11:00', 3, 3, 0, 0), (2749, '2021-02-20', 5, 1, '8:00', '8:00', '11:00', 3, 3, 0, 0)]]
[]
[[], [], [], [], [], []]
[]
[[(403, '2021-02-15', 0, 3, 15, 15, 0, '8:00', '8:00', 0)], [(404, '2021-02-